# Selectivity categories for connectivity results

In [13]:
import re
import h5py
import numpy as np
import pandas as pd

from scipy import stats
from mne.stats import fdr_correction
from string import ascii_letters as abc
from itertools import product
from os.path import join as pjoin

import matplotlib
import matplotlib.pyplot as plt
import matplotlib.patches as mpatches
import warnings
warnings.simplefilter('ignore')

%matplotlib inline

# list of subject names
print(sujs)

['sub-9d783b836f5e', 'sub-14c725b6b803', 'sub-28e70e7c7fbb', 'sub-83ebd5328120', 'sub-cacae171ee15', 'sub-95a634be7e05', 'sub-26176ef8a8d0', 'sub-44375d501493', 'sub-a4e7fc9daa96', 'sub-c1b7ce54ce05', 'sub-3ef8645f99c5', 'sub-fccb4adbfadc', 'sub-ebf231d97f73', 'sub-e0bb6ccef2a5', 'sub-4247d6d6cdbf', 'sub-45a6830d263e', 'sub-82e330f8aadd', 'sub-c2a96116ddc4']


In [14]:
# shortcut to joining var strings
def jn(mlist, char=None):
    """Summary

    Parameters
    ----------
    mlist : list
       List of strings to concatenate.
    join : str, optional
       Character for concatenation.

    Returns
    -------
    Concatenated string
    """
    if char is None:
        string = '_'.join(mlist)
    else:
        string = char.join(mlist)

    return string

**Fixed variables** 

In [15]:
analysis = 'connectivity'
alpha = .01
h5_path = pjoin('/Volumes',
                'Transcend',
                'ispeech_motorspeech_transcend',
                'projects',
                'ispeech',
                'data',
                'data_h5', )

In [16]:
cat_df = {}
b_d = {}

*Lists*

In [17]:
sounds = ['speech', 'music']
hemis = ['left', 'right']

# all bands
bands = ['delta', 'theta', 'alpha', 'beta', 'lga', 'hfa']
bands_r = ((1, 4), (5, 8), (8, 12), (18, 30), (30, 50), (80, 120))

# previous bands (delta from 1, HFa envelope correlation)
p_bands = ['delta', 'hfa']

# new custom bands
c_bands = ['theta', 'alpha', 'beta', 'lga']

*Band inidices in morlet*

In [18]:
freqs = np.logspace(np.log2(1), np.log2(150), num=100, base=2)
for b, r in zip(bands, bands_r):
    idx = [(np.abs(freqs - value)).argmin() for value in r]
    idx = (idx[0], idx[1] + 1)
    b_d[b + '_morlet_i'] = idx
    print(b, r, idx, np.round(freqs, 2)[slice(idx[0], idx[1])])

delta (1, 4) (0, 28) [1.   1.05 1.11 1.16 1.22 1.29 1.35 1.43 1.5  1.58 1.66 1.74 1.84 1.93
 2.03 2.14 2.25 2.36 2.49 2.62 2.75 2.89 3.04 3.2  3.37 3.54 3.73 3.92]
theta (5, 8) (32, 42) [5.05 5.31 5.59 5.88 6.18 6.51 6.84 7.2  7.57 7.97]
alpha (8, 12) (41, 50) [ 7.97  8.38  8.81  9.27  9.75 10.26 10.79 11.35 11.94]
beta (18, 30) (57, 68) [17.9  18.83 19.81 20.84 21.92 23.06 24.25 25.51 26.84 28.23 29.7 ]
lga (30, 50) (67, 78) [29.7  31.24 32.86 34.57 36.36 38.25 40.23 42.32 44.52 46.83 49.26]
hfa (80, 120) (87, 96) [ 81.72  85.96  90.42  95.12 100.06 105.25 110.72 116.46 122.51]


*Band inidices in fourier*

In [19]:
ffreqs = np.round([2.199120351859256,
                   2.5989604158336665,
                   3.0987604958016792,
                   3.6985205917632946,
                   4.4982007197121145,
                   5.497800879648141,
                   6.597361055577768,
                   8.096761295481809,
                   9.79608156737305,
                   11.795281887245102,
                   14.394242303078768,
                   17.293082766893242,
                   21.091563374650143,
                   25.489804078368653,
                   30.78768492602959,
                   37.28508596561377,
                   45.281887245101956,
                   54.8780487804878,
                   66.47341063574571,
                   80.46781287485007,
                   97.56097560975608,
                   118.15273890443822,
                   143.14274290283885],
                  2)

for b, r in zip(bands, bands_r):
    idx = [(np.abs(ffreqs - value)).argmin() for value in r]
    idx = (idx[0], idx[1] + 1)
    b_d[b + '_fourier_i'] = idx
    print(b, r, idx, ffreqs[slice(idx[0], idx[1])])

delta (1, 4) (0, 4) [2.2 2.6 3.1 3.7]
theta (5, 8) (4, 8) [4.5 5.5 6.6 8.1]
alpha (8, 12) (7, 10) [ 8.1  9.8 11.8]
beta (18, 30) (11, 15) [17.29 21.09 25.49 30.79]
lga (30, 50) (14, 17) [30.79 37.29 45.28]
hfa (80, 120) (19, 22) [ 80.47  97.56 118.15]


*Some little functions*

In [20]:
def get_name(data, analysis=analysis, condition=None):
    if condition:
        cname = jn([analysis, 'left_fourier', condition, data, 'sign'])
    else:
        cname = jn([analysis, 'difference', data, 'sign'])
    return cname

*Plotting colors and cmaps*

In [21]:
color = {
    'speech': [  # red
        np.array((242, 152, 154)).reshape(1, -1),
        np.array((254, 75, 73)).reshape(1, -1),
        np.array((219, 129, 130)).reshape(1, -1),
    ],
    'music': [  # blue
        np.array((148, 210, 221)).reshape(1, -1),
        np.array((43, 183, 200)).reshape(1, -1),
        np.array((114, 183, 194)).reshape(1, -1),
    ],
    'shared': [  # yellow
        np.array((243, 222, 168)).reshape(1, -1),
        np.array((255, 214, 102)).reshape(1, -1),
        np.array((220, 199, 145)).reshape(1, -1),
    ],
    'neither_grey': [  # grey
        np.array((230, 229, 234)).reshape(1, -1),
        np.array((184, 183, 187)).reshape(1, -1),
        np.array((132, 131, 134)).reshape(1, -1),
    ]}

color['shared'][1] = np.array([[255, 255, 255]])

## Prepare DataFrame

### **Collect base data** from presaved DF and add data of interest

The conditions of our ethics approval do not permit public archiving of anonymised study data. Readers seeking access to the data should contact the lead author. Access will be granted to named individuals in accordance with ethical procedures governing the reuse of clinical data, including completion of a formal data sharing agreement.

In [22]:
# collect ispeech dataframe and add other infos
path = pjoin(h5_path, 'h5_df')
with pd.HDFStore(pjoin(path, 'ispeech_base_df.h5'), mode='r') as store:
    df = store.select('df')

*Add column to be able to, in the brain plots, plot deeper channels first*

In [23]:
df['chorder'] = [min(re.findall(r'\d+', c)) for c in df.chnames]

### Add **main effects** for **custom bands** (theta, alpha, beta, low gamma)

### Add **difference surrogate effects** for all bands

Check counts

In [14]:
for band in bands:
    name = '%s_difference_%s_sign' % (analysis, band)
    print(band, '->',
          'total: %s;' % len(df.loc[~(df[name].isna())]),
          'speech: %s;' % len(df.loc[(df[name] > 0)]),
          'music: %s;' % len(df.loc[(df[name] < 0)]))

delta -> total: 1055; speech: 507; music: 548;
theta -> total: 665; speech: 278; music: 387;
alpha -> total: 530; speech: 251; music: 279;
beta -> total: 161; speech: 88; music: 73;
lga -> total: 81; speech: 41; music: 40;
hfa -> total: 42; speech: 38; music: 4;


---
---
### Prepare intersections

***shared***:
- main effect for both significant and no difference effect (green) -> both_no
    
***almost shared***:
- main effect for speech but no difference effect -> sp_no
- main effect for music but no difference effect -> mu_no
    
***preferred***:
- main effect for both but difference effect for speech -> both_sp 
- main effect for both but difference effect for music -> both_mu 

***selective***:
- main effect only for speech plus difference effect (red) -> sp_sp
- main effect only for music plus difference (effect (blue) -> mu_mu
    
***impossible situation but check for it***:
- neither but difference speech -> no_sp
- neither but difference music -> no_mu
---

***shared***

In [15]:
include_almost_shared = True
for band in bands:
    temp = df
    columns = [get_name(data=band, condition=sound) for sound in sounds]

    print(band, len(temp.loc[(temp[columns].notnull().any(axis=1))]))

    # including almost shared
    if include_almost_shared:
        cat_df['shared_' + band] = temp.loc[(temp[columns].notnull().any(
            axis=1)) & ~(temp[get_name(data=band)].notnull())]

    # excluding almost shared
    else:
        cat_df['shared_' + band] = temp.loc[(temp[columns].notnull().all(
            axis=1)) & ~(temp[get_name(data=band)].notnull())]

    print(band, '-> shared %s' % len(cat_df['shared_' + band]))

delta 811
delta -> shared 281
theta 756
theta -> shared 381
alpha 694
alpha -> shared 374
beta 215
beta -> shared 152
lga 148
lga -> shared 113
hfa 217
hfa -> shared 178


***preferred***

In [16]:
for band in bands:
    temp = df
    columns = [get_name(data=band, condition=sound) for sound in sounds]
    cat_df['speech_preferred_' + band] = temp.loc[(
        temp[columns].notnull().all(axis=1)) & (temp[get_name(data=band)] > 0)]
    cat_df['music_preferred_' + band] = temp.loc[(
        temp[columns].notnull().all(axis=1)) & (temp[get_name(data=band)] < 0)]
    print(band, '->',
          'speech: %s;' % len(cat_df['speech_preferred_' + band]),
          'music: %s;' % len(cat_df['music_preferred_' + band]))

delta -> speech: 134; music: 166;
theta -> speech: 105; music: 125;
alpha -> speech: 107; music: 97;
beta -> speech: 29; music: 15;
lga -> speech: 15; music: 7;
hfa -> speech: 28; music: 0;


***selective***

In [17]:
for band in bands:
    temp = df
    cat_df['speech_selective_' + band] = temp.loc[(temp[get_name(data=band, condition='speech')] > 0) & ~(
        temp[get_name(data=band, condition='music')] > 0) & (temp[get_name(data=band)] > 0)]
    cat_df['music_selective_' + band] = temp.loc[~(temp[get_name(data=band, condition='speech')] > 0) & (
        temp[get_name(data=band, condition='music')] > 0) & (temp[get_name(data=band)] < 0)]
    print(band, '->',
          'speech: %s;' % len(cat_df['speech_selective_' + band]),
          'music: %s;' % len(cat_df['music_selective_' + band]))

delta -> speech: 87; music: 124;
theta -> speech: 43; music: 84;
alpha -> speech: 38; music: 64;
beta -> speech: 11; music: 4;
lga -> speech: 6; music: 5;
hfa -> speech: 9; music: 2;


***impossible situation but check for it***:
- neither but difference speech -> no_sp
- neither but difference music -> no_mu

In [18]:
for band in bands:
    temp = df
    columns = [get_name(data=band, condition=sound) for sound in sounds]
    cat_df['weird_' + band] = temp.loc[(~temp[columns].notnull().any(
        axis=1)) & (temp[get_name(data=band)].notnull())]
    print(band, '-> weird: %s' % len(cat_df['weird_' + band]))

delta -> weird: 525
theta -> weird: 290
alpha -> weird: 210
beta -> weird: 98
lga -> weird: 46
hfa -> weird: 3


## Grid: **Electrodes distribution** (MNI) and **overview categories** (nested pies) per band

Some **plotting prefixes**

In [19]:
# fontsizes
fticks = 27
flabels = 35
fcount = 52
lwidth = 2  # line width
size = .3  # pie sizes

# filters to loop over
visuals = ['shared', 'preferred', 'selective']
bars = ['shared', 'speech_preferred', 'music_preferred',
        'speech_selective', 'music_selective']

emdash = u'\u2014'
hatchp = 'x'

outer_colors = [np.array((255, 255, 255)).reshape(1, -1) / 255,
                np.array((52, 52, 53)).reshape(1, -1) / 255,
                color['neither_grey'][2] / 255]
inner_colors = [color['shared'][1] / 255] + [color[sound]
                                             [1] / 255 for i, sound in product(range(2)[::-1], sounds)]

### Now including network in color of conditions

In [29]:
fig3 = plt.figure(figsize=(27, 37), constrained_layout=False)

for z, band in enumerate(bands):
    gs = fig3.add_gridspec(2, 2,
                           wspace=-.05,
                           hspace=-.3,
                           left=0 if z < 3 else .55,
                           right=.45 if z < 3 else 1,
                           bottom=(3 - z % 3) * .3,
                           top=((3 - z % 3) + 1) * .3)

    band_name = 'HFa' if band == 'hfa' else 'low gamma' if band == 'lga' else band

    # Brain figure
    ##############################################################################
    for o, orientation in enumerate(brains):

        # which axes
        con_orientation = fig3.add_subplot(gs[1, o])
        axes = con_orientation

        # collect stored mayavi brain images
        with h5py.File(pjoin(path, 'mayavi_electrodes.hdf5'), 'r') as hf:
            im = hf[orientation]['imp'][...]
        axes.imshow(im)

        for j in range(20):
            for v, viz in enumerate(visuals):
                if viz == 'preferred':
                    continue
                for sound in sounds:
                    if viz != 'shared':
                        label = jn([sound, viz, band])
                    else:
                        if sound == 'music':
                            continue
                        label = jn([viz, band])
                    # filter dataframe and move on if nothing matches
                    t_df = cat_df[label]
                    t_df = t_df.loc[(t_df['chorder'] == str(j))]
                    if len(t_df) == 0:
                        continue

                    # connecting seed to subject
                    for subject in sujs:
                        temp_df = t_df.loc[(t_df['subject'] == subject)]

                        # collect coordinates
                        df_x = temp_df[jn([orientation, 'x'])].values
                        df_y = temp_df[jn([orientation, 'y'])].values
                        left_i, right_i = [], []
                        for i, ch in enumerate(temp_df['chnames'].values):
                            if "'" in ch:
                                left_i.append(i)
                            else:
                                right_i.append(i)
                        if orientation in hemis:
                            x_h = df_x[left_i] if orientation == 'left' else df_x[right_i]
                            y_h = df_y[left_i] if orientation == 'left' else df_y[right_i]
                        else:
                            x_h = df_x
                            y_h = df_y

                        # plot elecs scatterplot
                        axes.scatter(x_h,
                                     y_h,
                                     zorder=3,
                                     edgecolors='k',
                                     color=outer_colors[v] if 'selective' not in viz else color[label.split('_')[
                                         0]][1] / 255,
                                     label='%s %s' % (len(x_h), label),
                                     s=120 * np.ones(len(x_h)))

                        if v == 0 and orientation == 'left':
                            s_seed = seed_df.loc[(
                                seed_df['subject'] == subject)]

                            # collect coordinates
                            x_seed = s_seed[jn([orientation, 'x'])].values
                            y_seed = s_seed[jn([orientation, 'y'])].values

                            # plot elecs scatterplot
                            axes.scatter(x_seed,
                                         y_seed,
                                         zorder=3,
                                         linewidth=.7,
                                         edgecolors='k',
                                         color=np.array(
                                             [255, 214, 102, 120])/255,
                                         label='%s %s' % (len(x_seed), label),
                                         alpha=1 if orientation == 'left' else 0,
                                         s=50 * np.ones(len(x_seed)))

                        axes.plot([x_h, [x_seed] * len(x_h)],
                                  [y_h, [y_seed] * len(x_h)],
                                  linewidth=1,
                                  zorder=2,
                                  alpha=1,
                                  color=outer_colors[v] if 'selective' not in viz else color[label.split('_')[
                                      0]][1] / 255)

                        # clean up subplot
                        axes.set_axis_off()

    # Bad title figure
    ##############################################################################
    band_title = fig3.add_subplot(gs[0, 0])
    axes = band_title
    axes.set_title(abc[z].upper(), fontsize=fcount, loc='left', y=0.7)
    axes.text(.5,
              .5,
              '%s %s \n(%s %s %s Hz)' % (
                  band_name,
                  'band' if band != 'hfa' else '',
                  bands_r[z][0],
                  emdash,
                  bands_r[z][1]),
              fontsize=fcount-10,
              ha='center', va='center')
    # clean up subplot
    axes.set_axis_off()

    # Nested pie figure
    ##############################################################################
    nested_pie = fig3.add_subplot(gs[0, 1])
    # Turn off axes and set axes limits
    axes = nested_pie

    # prepare counts per category for the rings
    inner_len = [len(cat_df[jn([bar, band])]) for bar in bars]
    outer_len = [len(cat_df[jn(['shared', band])])] + [len(cat_df[jn(['speech', viz, band])]
                                                           ) + len(cat_df[jn(['music', viz, band])]) for viz in visuals[1:]]

    # sum of significant electrodes
    all_sum = np.array([len(cat_df[jn([bar, band])]) for bar in bars]).sum()

    # percentage significant electrodes over whole brain
    # in total and per category
    p_overbrain = np.round((all_sum / len(df)) * 100, 1)
    percentages = ['%s%%' % np.round((j / all_sum) * 100, 1)
                   for j in outer_len]

    # plot outer pie
    axes.pie(outer_len,
             radius=1,
             colors=outer_colors,
             labels=percentages,
             textprops={'fontsize': fticks},
             wedgeprops=dict(width=size, edgecolor='k', linewidth=lwidth))

    # inner pie
    inner = axes.pie(inner_len,
                     radius=1 - size,
                     colors=inner_colors,
                     wedgeprops=dict(width=size, edgecolor='k', linewidth=lwidth))

    # add hatch pattern to preferred
    for h in range(2):
        inner[0][h+1].set_hatch(hatchp)
        inner[0][h+1].set_edgecolor(np.array((52, 52, 53)
                                             ).reshape(1, -1) / 255)

    axes.text(0., 0.,
              '%s%%' % (p_overbrain),
              fontsize=flabels,
              ha='center',
              va='center')


# prepare legend
###########################################################################################
gs = fig3.add_gridspec(1, 2, top=1.25)
legend_s = fig3.add_subplot(gs[0, :])
axes = legend_s

# legend patches
sounds_l = [mpatches.Patch(facecolor=color[sound][1] /
                           255, label=sound, edgecolor='k', linewidth=lwidth) for sound in sounds]
category_l = [mpatches.Patch(facecolor=outer_colors[i], edgecolor='k', label=cat)
              for i, cat in enumerate(visuals)]
axes.legend(handles=sounds_l + category_l,
            ncol=6,
            loc='upper right',
            labelspacing=.7)
axes.set_axis_off()